In [418]:
import pandas as pd
import numpy as np
import math as math
import statistics
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score
import datetime
from sklearn.metrics import confusion_matrix
import matplotlib.pyplot as plt
from sklearn.metrics import log_loss
from sklearn.preprocessing import StandardScaler
from mlxtend.plotting import plot_decision_regions
import time

pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('max_colwidth', 1000)  #
pd.set_option('display.width', 150)

# from functions import *
#https://www.nba.com/stats/teams/boxscores-scoring

In [419]:
def convertDateColumn(df):
    locationToInsert = df.columns.get_loc('DATE')+1
    dates = pd.to_datetime(df['DATE'],format="%m/%d/%y").dt.date
    df = df.drop(columns='DATE')
    df.insert(locationToInsert,'DATE',dates)
    df = df.sort_values(by=['DATE','GAMEID']).reset_index(drop=True)
    return df
def featureEngineering(boxScoreType,df):
    if boxScoreType == 'TRADITIONAL':
        featuresToAddDict = {'OPPT':[],'PTSA':[],'2FGA':[],'2FGM':[],'2FG%':[],
                             'RESULT':[],'PTSDELTA':[],'H/A':[]}
        for i in range(len(df)):
            featuresToAddDict['OPPT'].append(df.iloc[i]['MATCH'][-3:])
            if i % 2 == 0: featuresToAddDict['PTSA'].append(df.iloc[i+1]['PTS'])
            else: featuresToAddDict['PTSA'].append(df.iloc[i-1]['PTS'])
            if df['W/L'][i] == 'L': featuresToAddDict['RESULT'].append(0)
            else: featuresToAddDict['RESULT'].append(1)
            featuresToAddDict['H/A'].append(df['MATCH'][i].count('vs'))
        df.insert(df.columns.get_loc('TEAM')+1,'OPPT',featuresToAddDict['OPPT'])
        df.insert(df.columns.get_loc('PTS')+1,'PTSA',featuresToAddDict['PTSA'])
        df.insert(df.columns.get_loc('FG%')+1,'2FGM',df['FGM'] - df['3PM'])
        df.insert(df.columns.get_loc('FG%')+1,'2FGA',df['FGA'] - df['3PA']) 
        df.insert(df.columns.get_loc('FG%')+1,'2FG%',df['2FGM']/df['2FGA'])
        df.insert(df.columns.get_loc('W/L')+1,'RESULT',featuresToAddDict['RESULT'])
        df = df.drop(columns=['W/L'])
        df.insert(df.columns.get_loc('PTSA')+1,'PTSDELTA',df['PTS']-df['PTSA'])
        df.insert(df.columns.get_loc('DATE')+1,'H/A',featuresToAddDict['H/A'])
        return df
    else:
        featuresToAddDict = {"OPPT":[],"RESULT":[],"H/A":[]}
        for i in range(len(df)):
            featuresToAddDict["OPPT"].append(df.iloc[i]['MATCH'][-3:])
            if df['W/L'][i] == 'L': featuresToAddDict["RESULT"].append(0)
            else: featuresToAddDict["RESULT"].append(1)
            featuresToAddDict["H/A"].append(df['MATCH'][i].count('vs'))
        df.insert(df.columns.get_loc('TEAM')+1,'OPPT',featuresToAddDict["OPPT"])
        df.insert(df.columns.get_loc('W/L')+1,'RESULT',featuresToAddDict["RESULT"])
        df = df.drop(columns=['W/L'])
        df.insert(df.columns.get_loc('DATE')+1,'H/A',featuresToAddDict["H/A"])
        return df
def addDaysOff(teamsDict):
    for team in list(teamsDict.keys()):
        daysOff = []
        daysOff.append(np.nan)
        for i in range(1,len(teamsDict[team]['DATE'])):
            date = teamsDict[team]['DATE'][i]
            prevDate = teamsDict[team]['DATE'][i-1] + datetime.timedelta(1)
            daysOff.append((date - prevDate).days)
        teamsDict[team]['DAYSOFF'] = daysOff
def addAdditionalFeatures(df,teamsDict):
    teams = []
    for team in list(teamsDict.keys()):
        teamDF = df[df['TEAM'] == team]
        startingIndex = len(list(df.columns))
        additionalFeatures = list(teamsDict[team].keys())[startingIndex:]
        for feature in additionalFeatures:
            teamDF = pd.concat([teamDF,
                                pd.DataFrame(teamsDict[team][feature],columns=[feature],index=teamDF.index.values)],axis=1)
        teams.append(teamDF)
    return pd.concat(teams)

def getTeamData(boxScoreType,df):
    teamsDict = {}
    features = df.columns.values
    
    if boxScoreType == 'TRADITIONAL': additionalFeatures = ['Ws','Ls','GP','W%','L%','AVGPTS','AVGPTSA']
    else: additionalFeatures = ['GP']
    for team in np.unique(df['TEAM']):
        teamsDict[team] = {}
    for team in np.unique(df['TEAM']):
        for feature in features:
            teamsDict[team][feature] = []
        for feature in additionalFeatures:
            teamsDict[team][feature] = []
    for i in range(len(df)):
        for feature in features:
            team = df.iloc[i]['TEAM']
            teamsDict[team][feature].append(df.iloc[i][feature])
        for feature in additionalFeatures:
            if feature == 'Ws': teamsDict[team][feature].append(teamsDict[team]['RESULT'].count(1))
            if feature == 'Ls': teamsDict[team][feature].append(teamsDict[team]['RESULT'].count(0))
            if feature == 'GP': teamsDict[team][feature].append(len(teamsDict[team]['RESULT']))
            if feature == 'W%': teamsDict[team][feature].append(teamsDict[team]['Ws'][-1]/teamsDict[team]['GP'][-1])
            if feature == 'L%': teamsDict[team][feature].append(teamsDict[team]['Ls'][-1]/teamsDict[team]['GP'][-1])
            if feature == 'AVGPTS': teamsDict[team][feature].append(np.mean(teamsDict[team]['PTS']))
            if feature == 'AVGPTSA': teamsDict[team][feature].append(np.mean(teamsDict[team]['PTSA']))
    return teamsDict

def addMovingAverageLx(featureStringsDict,teamDict,x):
    for team in list(teamsDict.keys()):
        for feature in featureStringsDict.keys():
            ma = []
            for _ in range(x): ma.append(np.nan)
            for maRange in range(0,len(teamsDict[team][feature])-x):
                ma.append(np.mean(teamsDict[team][feature][maRange:(x+maRange)]))
            teamsDict[team][featureStringsDict[feature].replace('x',str(x))] = ma
                
def addPercentMovingAverageLx(featureStringsDict,teamsDict,x):
    for team in list(teamsDict.keys()):
        for features in featureStringsDict.keys():
            ma = []
            for _ in range(x): ma.append(np.nan)
            for maRange in range(0,len(teamsDict[team][features[0]])-x):
                num = np.sum(teamsDict[team][features[0]][maRange:(x+maRange)])
                dem = np.sum(teamsDict[team][features[1]][maRange:(x+maRange)])
                ma.append(num/dem)
            teamsDict[team][featureStringsDict[features].replace('x',str(x))] = ma

# Traditional.csv

In [420]:
start_time = time.time()
traditionalDF = pd.read_csv('/Users/olutosinfashusi/jupyter/csv/fromNBADOTCOM/2023-24/byGame/Traditional.csv')
traditionalDF = convertDateColumn(traditionalDF)
traditionalDF = featureEngineering('TRADITIONAL',traditionalDF)
teamsDict = getTeamData('TRADITIONAL',traditionalDF)
print("%s seconds" % (time.time() - start_time))

33.51529026031494 seconds


In [421]:
# start_time = time.time()
# trainDF = pd.read_csv(
#     '/Users/olutosinfashusi/jupyter/csv/fromNBADOTCOM/2023-24/byGame/Traditional.csv'
# )
# trainDF = convertCSVDateColumn(trainDF)
# FE_trainDF = featureEngineering(trainDF)
# dict_FE_trainDF = getDataFromDataFrame(FE_trainDF)
# # getMovingAverageLx(dict_FE_trainDF,5)
# # getPercentMovingAverageLx(dict_FE_trainDF,5)
# # getMovingAverageLx(dict_FE_trainDF,4)
# # getPercentMovingAverageLx(dict_FE_trainDF,4)
# # getMovingAverageLx(dict_FE_trainDF,3)
# # getPercentMovingAverageLx(dict_FE_trainDF,3)
# # getMovingAverageLx(dict_FE_trainDF,2)
# # getPercentMovingAverageLx(dict_FE_trainDF,2)
# # getMovingAverageLx(dict_FE_trainDF,1)
# # getPercentMovingAverageLx(dict_FE_trainDF,1)
# # getDaysOff(dict_FE_trainDF)
# AF_FE_trainDF = addAdditionalFeatures(FE_trainDF, dict_FE_trainDF)
# print("%s seconds" % (time.time() - start_time))

In [422]:
NBAdf = traditionalDF.sort_values(by=['DATE', 'GAMEID', 'H/A']).reset_index(drop=True)
NBAteams = np.unique(NBAdf['TEAM'])

In [423]:
len(NBAdf)

2460

In [424]:
dict_ = {}
for team in NBAteams:
    dict_[team] = {}
    dict_[team]['FAV#'] = int
    dict_[team]['✅'] = int
    dict_[team]['❌'] = int

In [425]:
dict_ = {}
for team in NBAteams:
    dict_[team] = {}

for team in NBAteams:
    teamDF = NBAdf[NBAdf['TEAM'] == team]
    teamDF = teamDF[teamDF['SPREAD'] < 0]
    dict_[team]['#FAV'] = len(teamDF[teamDF['SPREAD'] < 0])
    dict_[team]['BEAT SPEAD'] = sum(abs(teamDF['SPREAD']) < teamDF['PTSDELTA'])
    dict_[team]['BEAT SPEAD%'] = dict_[team]['BEAT SPEAD'] / dict_[team]['#FAV']
    dict_[team]['LOST SPREAD'] = sum(abs(teamDF['SPREAD']) > teamDF['PTSDELTA'])
    dict_[team]['LOST SPREAD%'] = dict_[team]['LOST SPREAD'] / dict_[team]['#FAV']
    dict_[team]['PUSH'] = sum(abs(teamDF['SPREAD']) ==  teamDF['PTSDELTA'])
    dict_[team]['PUSH%'] = dict_[team]['PUSH'] / dict_[team]['#FAV']
    
# for team in NBAteams:
#     teamDF = NBAdf[NBAdf['TEAM'] == team]
#     teamDF = teamDF[teamDF['SPREAD'] < 0]
#     dict_[team]['#FAV'] = len(teamDF[teamDF['SPREAD'] < 0])
#     dict_[team]['BEAT SPREAD'] = 0
#     dict_[team]['LOST SPREAD'] = 0
#     dict_[team]['PUSH'] = 0
#     for i in range(len(teamDF)):
#         if teamDF.iloc[i]['PTSDELTA'] < 0: #lost
#             dict_[team]['LOST SPREAD'] = dict_[team]['LOST SPREAD'] + 1
#         if teamDF.iloc[i]['PTSDELTA'] > 0: #won
#             if np.abs(teamDF.iloc[i]['SPREAD']) > teamDF.iloc[i]['PTSDELTA']:
#                 dict_[team]['LOST SPREAD'] = dict_[team]['LOST SPREAD'] + 1
#             if np.abs(teamDF.iloc[i]['SPREAD']) == teamDF.iloc[i]['PTSDELTA']:
#                 dict_[team]['PUSH'] = dict_[team]['PUSH'] + 1
#             if np.abs(teamDF.iloc[i]['SPREAD']) < teamDF.iloc[i]['PTSDELTA']:
#                 dict_[team]['BEAT SPREAD'] = dict_[team]['BEAT SPREAD'] + 1
spreadResultsDF = pd.DataFrame(dict_).T

In [426]:
# teamDF = NBAdf[NBAdf['TEAM'] == 'ATL']
# teamDF = teamDF[teamDF['SPREAD'] < 0]
# teamDF.reset_index(drop=True).head()

In [427]:
# abs(teamDF.iloc[2]['SPREAD']) > teamDF.iloc[2]['PTSDELTA']

In [428]:
spreadResultsDF.head()

#FAV  BEAT SPEAD  BEAT SPEAD%  LOST SPREAD  LOST SPREAD%  PUSH     PUSH%
ATL  43.0        15.0     0.348837         27.0      0.627907   1.0  0.023256
BKN  27.0        14.0     0.518519         12.0      0.444444   1.0  0.037037
BOS  79.0        40.0     0.506329         34.0      0.430380   5.0  0.063291
CHA   6.0         1.0     0.166667          5.0      0.833333   0.0  0.000000
CHI  33.0        15.0     0.454545         17.0      0.515152   1.0  0.030303

In [429]:
dict_ = {}
for team in NBAteams:
    dict_[team] = {}
    dict_[team]['gamesFav+LostSpread'] = pd.DataFrame
    
for team in NBAteams:
    teamDF = NBAdf[NBAdf['TEAM'] == team]
    teamDF = teamDF[teamDF['SPREAD'] < 0]
    teamDF = teamDF.reset_index(drop=True)

    df = pd.DataFrame()
    for i in range(len(teamDF)):
        if teamDF.iloc[i]['PTSDELTA'] < 0:
            df = pd.concat([df,teamDF.iloc[i].to_frame().T],axis=0)
        if teamDF.iloc[i]['PTSDELTA'] > 0:
            if np.abs(teamDF.iloc[i]['SPREAD']) > teamDF.iloc[i]['PTSDELTA']:
                df = pd.concat([df,teamDF.iloc[i].to_frame().T],axis=0)
    dict_[team]['gamesFav+LostSpread'] = df.reset_index(drop=True)

In [452]:
print(NBAteams)
print(len(NBAteams))

['ATL' 'BKN' 'BOS' 'CHA' 'CHI' 'CLE' 'DAL' 'DEN' 'DET' 'GSW' 'HOU' 'IND'
 'LAC' 'LAL' 'MEM' 'MIA' 'MIL' 'MIN' 'NOP' 'NYK' 'OKC' 'ORL' 'PHI' 'PHX'
 'POR' 'SAC' 'SAS' 'TOR' 'UTA' 'WAS']
30


In [453]:
NBAdf[NBAdf['TEAM'] == 'ATL'].head(1)

TEAM OPPT      TEAMID      MATCH    GAMEID  RESULT        DATE  H/A  SPREAD    O/U  MIN  PTS  PTSA  PTSDELTA  FGM  FGA   FG%     2FG%  2FGA  2FGM  \
4  ATL  CHA  1610612737  ATL @ CHA  22300063       0  2023-10-25    0    -4.0  236.0  240  110   116        -6   39   93  41.9  0.53125    64    34   

   3PM  3PA   3P%  FTM  FTA   FT%  OREB  DREB  REB  AST  STL  BLK  TOV  PF  +/-  
4    5   29  17.2   27   33  81.8    12    30   42   24   12    1   12  19   -6

In [450]:
NBAdf[NBAdf['TEAM'] == 'WAS']

TEAM OPPT     TEAMID        MATCH    GAMEID  RESULT        DATE  H/A  SPREAD    O/U  MIN  PTS  PTSA  PTSDELTA  FGM  FGA   FG%      2FG%  2FGA  \
6     WAS  IND  161061276    WAS @ IND  22300064       0  2023-10-25    0     5.5  235.0  240  120   143       -23   44   96  45.8  0.486111    72   
57    WAS  MEM  161061276  WAS vs. MEM  22300089       1  2023-10-28    1     1.0  227.5  240  113   106         7   40   93  43.0  0.510638    47   
85    WAS  BOS  161061276  WAS vs. BOS  22300103       0  2023-10-30    1    10.0  229.0  240  107   126       -19   39   87  44.8  0.549020    51   
112   WAS  ATL  161061276    WAS @ ATL  22300117       0  2023-11-01    0     9.0  240.5  240  121   130        -9   51  101  50.5  0.672131    61   
146   WAS  MIA  161061276    WAS @ MIA  22300003       0  2023-11-03    0     8.5  224.5  240  114   121        -7   46   81  56.8  0.622642    53   
188   WAS  PHI  161061276    WAS @ PHI  22300148       0  2023-11-06    0    11.0  229.0  240  128   146       -18   49   96  51.0  0.564516    62   
206   WAS  CHA  161061276    WAS @ CHA  22300157       1  2023-11-08    0     2.0  239.0  240  132   116        16   47   97  48.5  0.537037    54   
241   WAS  CHA  161061276  WAS vs. CHA  22300009       0  2023-11-10    1    -3.5  240.5  240  117   124        -7   43   88  48.9  0.580000    50   
266   WAS  BKN  161061276    WAS @ BKN  22300178       0  2023-11-12    0     7.0  233.5  240   94   102        -8   33   88  37.5  0.489362    47   
288   WAS  TOR  161061276    WAS @ TOR  22300189       0  2023-11-13    0     8.0  230.5  240  107   111        -4   43   84  51.2  0.534483    58   
315   WAS  DAL  161061276  WAS vs. DAL  22300192       0  2023-11-15    1     3.5  243.5  240  117   130       -13   43   89  48.3  0.584906    53   
337   WAS  NYK  161061276  WAS vs. NYK  22300028       0  2023-11-17    1     7.0  225.5  240   99   120       -21   37   82  45.1  0.540000    50   
391   WAS  MIL  161061276  WAS vs. MIL  22300219       0  2023-11-20    1    10.0  246.0  240  129   142       -13   55   99  55.6  0.642857    70   
412   WAS  CHA  161061276    WAS @ CHA  22300225       0  2023-11-22    0     3.5  240.5  240  114   117        -3   44   97  45.4  0.507692    65   
452   WAS  MIL  161061276    WAS @ MIL  22300049       0  2023-11-24    0    13.5  248.0  240  128   131        -3   48  100  48.0  0.523810    63   
465   WAS  ATL  161061276  WAS vs. ATL  22300241       0  2023-11-25    1     9.5  248.5  240  108   136       -28   43   88  48.9  0.660000    50   
488   WAS  DET  161061276    WAS @ DET  22300253       1  2023-11-27    0     2.0  236.5  240  126   107        19   45   89  50.6  0.583333    60   
516   WAS  ORL  161061276    WAS @ ORL  22300259       0  2023-11-29    0    10.0  235.5  240  120   139       -19   41   87  47.1  0.517241    58   
546   WAS  ORL  161061276    WAS @ ORL  22300274       0  2023-12-01    0    10.5  236.0  240  125   130        -5   45   89  50.6  0.524590    61   
597   WAS  PHI  161061276  WAS vs. PHI  22301208       0  2023-12-06    1    10.5  241.5  240  126   131        -5   52   92  56.5  0.666667    57   
622   WAS  BKN  161061276    WAS @ BKN  22301219       0  2023-12-08    0     9.5  239.5  240   97   124       -27   38   91  41.8  0.551724    58   
648   WAS  PHI  161061276    WAS @ PHI  22300295       0  2023-12-11    0    13.5  243.5  240  101   146       -45   36   85  42.4  0.500000    54   
681   WAS  NOP  161061276  WAS vs. NOP  22300311       0  2023-12-13    1     7.0  240.0  240  122   142       -20   42   82  51.2  0.605263    38   
715   WAS  IND  161061276  WAS vs. IND  22300328       1  2023-12-15    1     8.0  260.0  240  137   123        14   52   92  56.5  0.600000    65   
752   WAS  PHX  161061276    WAS @ PHX  22300347       0  2023-12-17    0    13.0  245.5  240  108   112        -4   39   95  41.1  0.510204    49   
774   WAS  SAC  161061276    WAS @ SAC  22300358       0  2023-12-18    0    14.5  252.0  240  131   143 

In [431]:
def cleanBoxScore(boxScoreDF):
    if 'Unnamed: 22' in boxScoreDF.columns:
            boxScoreDF = boxScoreDF.drop(columns='Unnamed: 22')
    boxScoreDF['PLAYER']
    players = []
    for playerIter in range(5):
        players.append(boxScoreDF['PLAYER'].iloc[playerIter][:-1])
    for playerIter in range(5,len(boxScoreDF)):
        players.append(boxScoreDF['PLAYER'].iloc[playerIter])
    boxScoreDF = boxScoreDF.drop(columns='PLAYER')
    boxScoreDF.insert(0,'PLAYER',players)
    boxScoreDF = boxScoreDF.reset_index(drop=True).dropna()
    rowsToDrop = []
    for i in range(len(boxScoreDF)):
        if 'DNP' in boxScoreDF.iloc[i]['MIN'] or ' ' in boxScoreDF.iloc[i]['MIN'] or 'SUSPENSION' in boxScoreDF.iloc[i]['MIN']:
            rowsToDrop.append(i)

    boxScoreDF = boxScoreDF.drop(rowsToDrop)
    boxScoreDF['PTS_'] = boxScoreDF['PTS'].astype(int)
    boxScoreDF = boxScoreDF.drop(columns='PTS')
    boxScoreDF = boxScoreDF.rename(columns={'PTS_':'PTS'})
    return boxScoreDF

In [462]:
dict_[team]['gamesFav+LostSpread']

TEAM OPPT      TEAMID        MATCH    GAMEID RESULT        DATE H/A SPREAD    O/U  MIN  PTS PTSA PTSDELTA FGM  FGA   FG%      2FG% 2FGA 2FGM 3PM  \
0   BKN  CHA  1610612751  BKN vs. CHA  22300266      0  2023-11-30   1   -9.0  223.0  240  128  129       -1  52  105  49.5  0.550725   69   38  14   
1   BKN  UTA  1610612751    BKN @ UTA  22300357      0  2023-12-18   0   -3.5  233.0  240  108  125      -17  39   90  43.3   0.45098   51   23  16   
2   BKN  DET  1610612751    BKN @ DET  22300406      1  2023-12-26   0   -6.5  228.5  240  118  112        6  41   82  50.0  0.533333   60   32   9   
3   BKN  WAS  1610612751    BKN @ WAS  22300430      0  2023-12-29   0   -6.0  242.0  240  104  110       -6  39   91  42.9   0.47619   63   30   9   
4   BKN  POR  1610612751  BKN vs. POR  22300498      0  2024-01-07   1   -9.0  226.5  265  127  134       -7  46   91  50.5  0.592593   54   32  14   
5   BKN  POR  1610612751    BKN @ POR  22300578      0  2024-01-17   0   -5.0  221.5  240  103  105       -2  35   73  47.9  0.571429   35   20  15   
6   BKN  HOU  1610612751  BKN vs. HOU  22300645      1  2024-01-27   1   -4.0  221.5  240  106  104        2  36   74  48.6       0.6   40   24  12   
7   BKN  MEM  1610612751  BKN vs. MEM  22300879      0  2024-03-04   1   -9.5  206.0  240  102  106       -4  35   79  44.3  0.540541   37   20  15   
8   BKN  DET  1610612751    BKN @ DET  22300902      0  2024-03-07   0   -2.5  216.0  240  112  118       -6  41   84  48.8   0.55814   43   24  17   
9   BKN  CHA  1610612751    BKN @ CHA  22300918      0  2024-03-09   0   -6.5  207.5  240   99  110      -11  36   90  40.0  0.458333   48   22  14   
10  BKN  WAS  1610612751    BKN @ WAS  22301050      1  2024-03-27   0   -4.0  220.5  265  122  119        3  47   98  48.0  0.569231   65   37  10   
11  BKN  TOR  1610612751  BKN vs. TOR  22301160      1  2024-04-10   1  -12.0  220.5  240  106  102        4  38   86  44.2      0.54   50   27  11   

   3PA   3P% FTM FTA   FT% OREB DREB REB AST STL BLK TOV  PF  +/-  
0   36  38.9  10  15  66.7   22   30  52  21   6   4   9  11   -1  
1   39  41.0  14  20  70.0   11   25  36  25   4   9  14  17  -17  
2   22  40.9  27  43  62.8    7   35  42  22   6   7   9  22    6  
3   28  32.1  17  27  63.0   18   36  54  24   5   4  10  13   -6  
4   37  37.8  21  25  84.0    9   35  44  29   7   7  16  25   -7  
5   38  39.5  18  27  66.7    6   27  33  28   9   3  11  14   -2  
6   34  35.3  22  37  59.5    2   38  40  24  11   6  19  22    2  
7   42  35.7  17  30  56.7   12   21  33  27  10   6  13  20   -4  
8   41  41.5  13  18  72.2    4   24  28  24  12   4  14  17   -6  
9   42  33.3  13  17  76.5   16   25  41  22   4   2  16  14  -11  
10  33  30.3  18  23  78.3   10   35  45  24   8   9   8  16    3  
11  36  30.6  19  24  79.2   14   42  56  25   4  15  15  16    4

In [465]:
results = []
resultsDict = {}
GAMEIDs = []
players = []

for team in NBAteams:
    resultsDict[team] = []
for team in NBAteams:
    print(team)
    dict_[team]['gamesFav+LostSpread'].head()
    teamDF = dict_[team]['gamesFav+LostSpread']
    dateOfFirstGame = NBAdf[NBAdf['TEAM'] == team].head(1)['DATE'].values[0]
    teamDF = teamDF[teamDF['DATE'] > dateOfFirstGame]
    teamDF = teamDF.reset_index(drop=True);
    
    for i in range (len(teamDF)):
        
        GAMEID = str(teamDF.iloc[i]['GAMEID'])
        GAMEIDs.append(GAMEID)
        #print(GAMEID)
        
        boxScoreDF = pd.read_csv('/Users/olutosinfashusi/jupyter/csv/boxScoreCSV/boxScoreCSVs/'+ GAMEID +'.csv')#.fillna(' ')
        #print(boxScoreDF['PLAYER'])
        #STOP
        boxScoreDF = boxScoreDF[boxScoreDF['TEAM'] ==  team]
        boxScoreDF.insert(1,'OPPT',teamDF.iloc[i]['OPPT'])
        boxScoreDF = boxScoreDF.reset_index(drop=True).dropna()
        boxScoreDF = cleanBoxScore(boxScoreDF);

        prevGamesDF = NBAdf[NBAdf['TEAM'] == team]
        prevGamesDF  = prevGamesDF[prevGamesDF['DATE'] < teamDF.iloc[i]['DATE']]
        prevGamesDF.reset_index(drop=True)
        
        prevGameIDs = prevGamesDF['GAMEID'].values
        prevOppts = prevGamesDF['OPPT'].values
        
        prevBoxScoresDF = pd.DataFrame()
        for prevIter in range (len(prevGameIDs)):
            GAMEID = str(prevGameIDs[prevIter])
            #print('PREV:',GAMEID)
            prevBoxScoreDF = pd.read_csv('/Users/olutosinfashusi/jupyter/csv/boxScoreCSV/boxScoreCSVs/'+ GAMEID +'.csv')#.fillna(' ')
            prevBoxScoreDF = prevBoxScoreDF[prevBoxScoreDF['TEAM'] == team]
            prevBoxScoreDF.insert(1,'OPPT',prevOppts[prevIter])
            prevBoxScoreDF = cleanBoxScore(prevBoxScoreDF)
            prevBoxScoresDF = pd.concat([prevBoxScoresDF,prevBoxScoreDF],axis=0)
        players.append(prevBoxScoresDF['PLAYER'].values)
        prevBoxScoresDF.groupby('PLAYER')['PTS'].mean()
        boxScoreDF.groupby('PLAYER')['PTS'].mean()
        prevAVGPTS = round(pd.DataFrame(prevBoxScoresDF.groupby("PLAYER")['PTS'].mean()),1)

        prevAVGPTS = prevAVGPTS.rename(columns={'PTS':'PREV AVG PTS'})
        df = pd.DataFrame()
        df = pd.concat([boxScoreDF.groupby("PLAYER")['PTS'].mean(),
                        prevAVGPTS.groupby("PLAYER")['PREV AVG PTS'].mean()],axis=1).dropna()
        df['TEAM'] = teamDF.iloc[i]['TEAM']
        df['DATE'] = teamDF.iloc[i]['DATE']
        df['OPPT'] = teamDF.iloc[i]['OPPT']
        df['GAMEID'] = teamDF.iloc[i]['GAMEID']
        df['PTSDELTA'] = teamDF.iloc[i]['PTSDELTA']
        df['SPREAD'] = teamDF.iloc[i]['SPREAD']
        
#         PTS_ = []
#         for k in range(len(df['PTS'])):
#             PTS_.append(round(df['PTS'].values[k]))
#         df = df.drop(columns=['PTS'])
#         df.insert(0,'PTS', PTS_)
        resultsDict[team].append(df)

ATL
BKN
BOS
CHA
CHI
CLE
DAL
DEN
DET
GSW
HOU
IND
LAC
LAL
MEM
MIA
MIL
MIN
NOP
NYK
OKC
ORL
PHI
PHX
POR
SAC
SAS
TOR
UTA
WAS


In [433]:
(2460/2)  / 2

615.0

In [441]:
players

[array(["De'Andre Hunter", 'Saddiq Bey', 'Clint Capela', 'Dejounte Murray',
        'Trae Young', 'Bogdan Bogdanovic', 'Jalen Johnson', 'AJ Griffin',
        'Onyeka Okongwu', "De'Andre Hunter", 'Saddiq Bey', 'Clint Capela',
        'Dejounte Murray', 'Trae Young', 'Bogdan Bogdanovic',
        'Jalen Johnson', 'AJ Griffin', 'Onyeka Okongwu', "De'Andre Hunter",
        'Jalen Johnson', 'Clint Capela', 'Dejounte Murray', 'Trae Young',
        'Bogdan Bogdanovic', 'Saddiq Bey', 'Onyeka Okongwu', 'AJ Griffin',
        'Trent Forrest', 'Bruno Fernando', 'Kobe Bufkin', 'Mouhamed Gueye',
        "De'Andre Hunter", 'Jalen Johnson', 'Clint Capela',
        'Dejounte Murray', 'Trae Young', 'Bogdan Bogdanovic', 'Saddiq Bey',
        'AJ Griffin', 'Onyeka Okongwu', 'Bruno Fernando', 'Mouhamed Gueye',
        'Kobe Bufkin', "De'Andre Hunter", 'Saddiq Bey', 'Clint Capela',
        'Dejounte Murray', 'Trae Young', 'Bogdan Bogdanovic',
        'Jalen Johnson', 'Onyeka Okongwu', 'AJ Griffin', "De'Andre

In [466]:
print(GAMEIDs[0])
print(GAMEIDs[-1])
print(len(GAMEIDs))

22300172
22301172
592


In [16]:
#len(players)

In [442]:
playerSet = set()
for i in range(len(players)):
    playerSet.update(set(players[i]))

In [444]:
playerSet

{'AJ Green',
 'AJ Griffin',
 'AJ Lawson',
 'Aaron Gordon',
 'Aaron Holiday',
 'Aaron Nesmith',
 'Aaron Wiggins',
 'Adam Flagler',
 'Adama Sanogo',
 'Admiral Schofield',
 'Al Horford',
 'Alec Burks',
 'Aleksej Pokusevski',
 'Alex Caruso',
 'Alex Fudge',
 'Alex Len',
 'Alondes Williams',
 'Alperen Sengun',
 'Amari Bailey',
 'Amen Thompson',
 'Amir Coffey',
 'Andre Drummond',
 'Andre Jackson Jr.',
 'Andrew Funk',
 'Andrew Nembhard',
 'Andrew Wiggins',
 'Anfernee Simons',
 'Anthony Black',
 'Anthony Davis',
 'Anthony Edwards',
 'Anthony Gill',
 'Armoni Brooks',
 'Ashton Hagans',
 'Ausar Thompson',
 'Austin Reaves',
 'Ayo Dosunmu',
 'Bam Adebayo',
 'Ben Sheppard',
 'Ben Simmons',
 'Bennedict Mathurin',
 'Bilal Coulibaly',
 'Bismack Biyombo',
 'Blake Wesley',
 'Boban Marjanovic',
 'Bobby Portis',
 'Bogdan Bogdanovic',
 'Bojan Bogdanovic',
 'Bol Bol',
 'Bones Hyland',
 'Bradley Beal',
 'Brandin Podziemski',
 'Brandon Boston Jr.',
 'Brandon Ingram',
 'Brandon Miller',
 'Brandon Williams',
 'Br

In [443]:
len(playerSet)

564

In [197]:
#resultsDict['ATL']

In [198]:
#resultsDict['BKN']

In [343]:
count = 0
for team in NBAteams:
    FLAG = []
    resultsDF = pd.DataFrame()
    for i in range (len(resultsDict[team])):
        resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
    for i in range(len(resultsDF)):
        if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
            FLAG.append('🚩')
        else: FLAG.append(' ')
    resultsDF['FLAG'] = FLAG
    resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')
    count = count+len(resultsDF[resultsDF['FLAG'] == '🚩'])

In [344]:
print(count)

219


In [345]:
allDF = pd.DataFrame()

In [346]:
team = 'ATL'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                  
Jalen Johnson   5.0          15.4  ATL  2024-01-13  WAS  22300543       -28    -8.0    🚩
Saddiq Bey      2.0          12.1  ATL  2023-11-09  ORL  22300172         1    -3.5    🚩
Trae Young     13.0          27.8  ATL  2024-01-12  IND  22300533       -18    -6.0    🚩
Trae Young     12.0          27.0  ATL  2024-02-14  CHA  22300777       -23    -7.0    🚩
Trae Young     11.0          26.7  ATL  2024-02-23  TOR  22300804        -2    -7.5    🚩
Trae Young     14.0          26.4  ATL  2024-04-10  CHA  22301159        -1    -8.5    🚩

In [347]:
team = 'BKN'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                    
Cam Thomas        9.0          20.7  BKN  2024-01-07  POR  22300498        -7    -9.0    🚩
Cam Thomas        8.0          20.6  BKN  2024-01-17  POR  22300578        -2    -5.0    🚩
Lonnie Walker IV  0.0          14.0  BKN  2024-01-07  POR  22300498        -7    -9.0    🚩
Lonnie Walker IV  0.0          12.0  BKN  2024-01-27  HOU  22300645         2    -4.0    🚩

In [348]:
team = 'BOS'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                       
Derrick White        2.0          16.0  BOS  2024-01-27  LAC  22300646       -19    -7.0    🚩
Derrick White        3.0          15.5  BOS  2024-03-05  CLE  22300886        -1    -8.5    🚩
Derrick White        4.0          15.8  BOS  2024-02-09  WAS  22300743         4   -18.0    🚩
Derrick White        2.0          15.4  BOS  2024-04-11  NYK  22301167        -9    -3.5    🚩
Jaylen Brown        12.0          22.9  BOS  2023-11-19  MEM  22300213         2   -12.0    🚩
Jaylen Brown         8.0          22.5  BOS  2024-01-27  LAC  22300646       -19    -7.0    🚩
Jaylen Brown         8.0          22.2  BOS  2024-02-01  LAL  22300684        -9   -15.5    🚩
Jaylen Brown        11.0          23.2  BOS  2023-11-08  PHI  22300159        -3    -2.5    🚩
Jayson Tatum        17.0          28.5  BOS  2023-11-17  TOR  22300031         3    -9.0    🚩
Jayson Tatum        15.0          27.3  BOS  2023-12-19  GSW  22300362        -6    -5.0    🚩
Jayson Tatum        17.0          27.2  BOS  2024-04-05  SAC  22301118         1    -9.5    🚩
Jayson Tatum        15.0          27.1  BOS  2024-03-07  DEN  22300906        -6    -2.0    🚩
Jayson Tatum        16.0          30.5  BOS  2023-11-08  PHI  22300159        -3    -2.5    🚩
Jayson Tatum        22.0          34.0  BOS  2023-10-27  MIA  22300080         8    -8.5    🚩
Jrue Holiday         2.0          12.6  BOS  2024-04-01  CHA  22301087        14   -18.5    🚩
Kristaps Porzingis   9.0          19.6  BOS  2023-11-24  ORL  22300043       -17    -5.0    🚩
Kristaps Porzingis  17.0          30.0  BOS  2023-10-27  MIA  22300080         8    -8.5    🚩

In [349]:
team = 'CHA'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                    
Gordon Hayward    4.0          15.1  CHA  2023-11-22  WAS  22300225         3    -3.5    🚩
Mark Williams     2.0          13.0  CHA  2023-10-27  DET  22300077       -12    -4.5    🚩
P.J. Washington  13.0          25.0  CHA  2023-10-27  DET  22300077       -12    -4.5    🚩

In [350]:
team = 'CHI'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                   
Coby White       0.0          16.0  CHI  2023-10-28  DET  22300088       -16    -2.5    🚩
Nikola Vucevic   5.0          18.0  CHI  2024-04-01  ATL  22301091       -12    -2.0    🚩
Zach LaVine     10.0          20.5  CHI  2024-01-13  SAS  22300548         6    -7.0    🚩

In [351]:
team = 'CLE'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                     
Caris LeVert       6.0          17.5  CLE  2023-11-25  LAL  22300242        -6    -4.0    🚩
Caris LeVert       5.0          15.5  CLE  2023-11-30  POR  22300265        -8   -12.5    🚩
Caris LeVert       4.0          15.3  CLE  2024-02-07  WAS  22300728         8   -11.5    🚩
Darius Garland     6.0          20.3  CLE  2023-11-25  LAL  22300242        -6    -4.0    🚩
Darius Garland     9.0          20.6  CLE  2024-02-01  MEM  22300687         7    -8.5    🚩
Darius Garland     8.0          18.2  CLE  2024-02-27  DAL  22300832         2    -4.0    🚩
Donovan Mitchell  20.0          32.5  CLE  2023-11-08  OKC  22300167        -8    -2.0    🚩
Donovan Mitchell  10.0          28.5  CLE  2023-11-26  TOR  22300251         3    -3.5    🚩
Donovan Mitchell  17.0          27.6  CLE  2024-01-07  SAS  22300497         2   -10.5    🚩
Donovan Mitchell  16.0          28.4  CLE  2024-02-25  WAS  22300820         9   -13.5    🚩
Donovan Mitchell  13.0          27.7  CLE  2024-03-16  HOU  22300967       -14    -5.0    🚩
Donovan Mitchell  12.0          27.4  CLE  2024-03-29  PHI  22301067         3    -7.0    🚩
Max Strus          8.0          27.0  CLE  2023-10-27  OKC  22300081        -3    -2.0    🚩
Max Strus          2.0          12.8  CLE  2024-01-31  DET  22300675         7   -13.5    🚩
Max Strus          2.0          12.6  CLE  2024-02-07  WAS  22300728         8   -11.5    🚩

In [352]:
team = 'DAL'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                      
Derrick Jones Jr.   0.0          10.2  DAL  2023-11-05  CHA  22300143         6   -11.5    🚩
Grant Williams      5.0          17.0  DAL  2023-10-27  BKN  22300084         5    -6.0    🚩
Kyrie Irving       10.0          24.6  DAL  2023-12-01  MEM  22300277       -14    -6.0    🚩
Luka Doncic        23.0          33.8  DAL  2023-11-05  CHA  22300143         6   -11.5    🚩
Luka Doncic        16.0          32.6  DAL  2023-11-14  NOP  22300022       -21    -3.5    🚩
Luka Doncic        19.0          33.9  DAL  2024-01-01  UTA  22300457       -37    -4.5    🚩
Luka Doncic        18.0          34.4  DAL  2024-03-19  SAS  22300994         6    -9.0    🚩
Tim Hardaway Jr.    6.0          17.9  DAL  2024-01-01  UTA  22300457       -37    -4.5    🚩
Tim Hardaway Jr.    5.0          17.7  DAL  2024-02-12  WAS  22300768         8   -12.0    🚩
Tim Hardaway Jr.    2.0          16.7  DAL  2024-03-03  PHI  22300871        -4    -7.5    🚩
Tim Hardaway Jr.    6.0          16.4  DAL  2024-03-05  IND  22300892       -17    -5.5    🚩
Tim Hardaway Jr.    5.0          15.7  DAL  2024-03-19  SAS  22300994         6    -9.0    🚩

In [353]:
team = 'DEN'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                             
Aaron Gordon               2.0          13.9  DEN  2023-11-24  HOU  22300048       -19    -3.0    🚩
Aaron Gordon               3.0          13.1  DEN  2023-12-08  HOU  22301224        -8    -9.0    🚩
Jamal Murray               9.0          19.9  DEN  2023-12-29  OKC  22300435       -26    -2.0    🚩
Jamal Murray               6.0          21.1  DEN  2024-02-29  MIA  22300855         6    -6.5    🚩
Kentavious Caldwell-Pope   8.0          20.0  DEN  2023-10-27  MEM  22300078         4    -6.0    🚩
Kentavious Caldwell-Pope   0.0          10.1  DEN  2024-03-29  MIN  22301071       -13    -3.0    🚩
Michael Porter Jr.         5.0          16.3  DEN  2024-01-10  UTA  22300524       -13    -6.5    🚩
Nikola Jokic              18.0          29.7  DEN  2023-11-19  CLE  22300210       -12    -4.5    🚩
Nikola Jokic               9.0          28.8  DEN  2023-11-20  DET  22300218         4    -9.5    🚩
Nikola Jokic              15.0          26.2  DEN  2024-02-14  SAC  22300786        -4    -5.5    🚩
Reggie Jackson             2.0          13.2  DEN  2023-12-23  CHA  22300390         7   -11.0    🚩
Reggie Jackson             2.0          12.8  DEN  2023-12-25  GSW  22300402         6    -7.5    🚩
Reggie Jackson             2.0          12.3  DEN  2024-01-04  GSW  22300478         3    -4.0    🚩

In [354]:
team = 'DET'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                    
Bojan Bogdanovic  8.0          21.1  DET  2023-12-21  UTA  22300374        -8    -2.0    🚩
Jalen Duren       0.0          13.9  DET  2024-04-01  MEM  22301088        -2    -3.0    🚩

In [355]:
team = 'GSW'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                     
Jonathan Kuminga   0.0          16.2  GSW  2024-04-14  UTA  22301198         7   -11.0    🚩
Klay Thompson      3.0          17.2  GSW  2023-12-30  DAL  22300444       -10    -4.0    🚩
Stephen Curry     21.0          33.5  GSW  2023-11-01  SAC  22300126         1    -6.5    🚩
Stephen Curry      7.0          29.0  GSW  2023-12-17  POR  22300348         4    -6.0    🚩
Stephen Curry     13.0          27.9  GSW  2023-12-28  MIA  22300426       -12    -6.5    🚩
Stephen Curry      9.0          27.6  GSW  2024-01-07  TOR  22300504       -15    -2.5    🚩
Stephen Curry     15.0          27.2  GSW  2024-03-07  CHI  22300907        -3    -8.5    🚩

In [356]:
team = 'HOU'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                     
Alperen Sengun    10.0          21.9  HOU  2024-01-31  NOP  22300679       -11    -1.0    🚩
Jabari Smith Jr.   0.0          13.8  HOU  2024-01-31  NOP  22300679       -11    -1.0    🚩
Jalen Green        5.0          17.1  HOU  2023-12-26  IND  22300409        -6    -3.0    🚩
Jalen Green        7.0          17.4  HOU  2024-01-20  UTA  22300598         1    -2.0    🚩
Jalen Green        4.0          18.3  HOU  2024-02-14  MEM  22300783        -8    -2.5    🚩
Jalen Green        3.0          19.8  HOU  2024-04-11  UTA  22301168        -3   -11.5    🚩

In [357]:
team = 'IND'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                       
Aaron Nesmith        5.0          16.5  IND  2023-10-30  CHI  22300102        -7    -3.5    🚩
Aaron Nesmith        0.0          11.2  IND  2023-11-19  ORL  22300209       -12    -4.5    🚩
Bennedict Mathurin   2.0          13.9  IND  2023-12-23  ORL  22300391        -7    -2.5    🚩
Bennedict Mathurin   2.0          14.5  IND  2024-01-19  POR  22300590        -3    -8.5    🚩
Bennedict Mathurin   0.0          14.1  IND  2024-02-12  CHA  22300761        -9   -10.0    🚩
Myles Turner         6.0          17.6  IND  2023-12-15  WAS  22300328       -14    -8.0    🚩
Obi Toppin           0.0          11.5  IND  2024-01-19  POR  22300590        -3    -8.5    🚩
Tyrese Haliburton   12.0          24.7  IND  2023-11-19  ORL  22300209       -12    -4.5    🚩
Tyrese Haliburton    5.0          22.9  IND  2024-02-08  GSW  22300733       -22    -6.0    🚩
Tyrese Haliburton    9.0          22.1  IND  2024-02-26  TOR  22300829        -8    -5.5    🚩

In [358]:
team = 'LAC'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                  
Ivica Zubac     6.0          20.0  LAC  2023-10-27  UTA  22300085        -2    -4.0    🚩
James Harden    4.0          17.2  LAC  2024-02-02  DET  22300688        11   -12.0    🚩
James Harden    6.0          17.0  LAC  2024-03-31  CHA  22301079        12   -14.0    🚩
James Harden    4.0          16.7  LAC  2024-04-12  UTA  22301184        -1   -15.5    🚩
Kawhi Leonard   6.0          24.0  LAC  2024-03-12  MIN  22300944       -18    -5.5    🚩
Norman Powell   2.0          13.5  LAC  2024-02-10  DET  22300749         6   -17.0    🚩
Paul George     6.0          25.2  LAC  2023-11-27  DEN  22300257        -9   -11.5    🚩
Paul George    13.0          23.1  LAC  2024-01-29  CLE  22300658       -10    -1.5    🚩
Paul George     7.0          22.5  LAC  2024-02-07  NOP  22300731       -11    -5.5    🚩
Paul George    10.0          22.7  LAC  2024-04-12  UTA  22301184        -1   -15.5    🚩

In [359]:
team = 'LAL'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                     
Anthony Davis      9.0          23.4  LAL  2023-11-15  SAC  22300198       -15    -1.0    🚩
Anthony Davis     14.0          24.9  LAL  2024-03-06  SAC  22300901       -10    -3.0    🚩
Anthony Davis      8.0          24.7  LAL  2024-03-16  GSW  22300973        -7    -1.5    🚩
D'Angelo Russell   4.0          18.4  LAL  2023-11-19  HOU  22300216         1    -6.5    🚩
D'Angelo Russell   2.0          15.8  LAL  2023-12-20  CHI  22300370       -16    -3.5    🚩
D'Angelo Russell   6.0          18.0  LAL  2024-03-13  SAC  22300954       -13    -2.5    🚩
D'Angelo Russell   4.0          18.2  LAL  2024-04-12  MEM  22301177         3   -16.0    🚩
LeBron James      12.0          25.4  LAL  2024-01-03  MIA  22300475       -14    -4.5    🚩
Rui Hachimura      0.0          11.6  LAL  2024-01-19  BKN  22300591       -18    -7.0    🚩
Taurean Prince     0.0          18.0  LAL  2023-10-26  PHX  22300076         5    -6.5    🚩
Taurean Prince     0.0          10.1  LAL  2024-01-03  MIA  22300475       -14    -4.5    🚩

In [360]:
team = 'MEM'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                      
Jaren Jackson Jr.  10.0          21.0  MEM  2024-01-02  SAS  22300460         8   -11.0    🚩

In [361]:
team = 'MIA'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                    
Bam Adebayo       8.0          21.0  MIA  2024-01-29  PHX  22300661       -13    -2.5    🚩
Caleb Martin      0.0          10.5  MIA  2024-03-22  NOP  22301013       -23    -3.0    🚩
Duncan Robinson   0.0          13.5  MIA  2024-01-29  PHX  22300661       -13    -2.5    🚩
Duncan Robinson   2.0          13.3  MIA  2024-04-04  PHI  22301111        -4    -2.5    🚩
Jaime Jaquez Jr.  2.0          13.8  MIA  2024-01-29  PHX  22300661       -13    -2.5    🚩
Jimmy Butler      8.0          21.5  MIA  2023-12-30  UTA  22300439        -8    -3.0    🚩
Kevin Love        0.0          10.1  MIA  2024-01-19  ATL  22300587        -1    -7.0    🚩

In [362]:
team = 'MIL'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                          
Bobby Portis            2.0          12.5  MIL  2023-11-24  WAS  22300049         3   -13.5    🚩
Damian Lillard          6.0          39.0  MIL  2023-10-29  ATL  22300097       -17    -7.5    🚩
Damian Lillard         12.0          24.3  MIL  2023-11-13  CHI  22300190         9    -9.5    🚩
Damian Lillard         14.0          25.6  MIL  2023-12-11  CHI  22300300         4   -11.5    🚩
Damian Lillard         13.0          25.9  MIL  2024-01-01  IND  22300454        -9    -8.0    🚩
Giannis Antetokounmpo  16.0          27.3  MIL  2023-11-01  TOR  22300116       -19    -4.5    🚩
Giannis Antetokounmpo  15.0          26.0  MIL  2023-11-08  DET  22300165         2   -12.0    🚩
Giannis Antetokounmpo  11.0          31.4  MIL  2023-12-19  SAS  22300361        13   -16.5    🚩
Khris Middleton         5.0          15.2  MIL  2024-04-07  NYK  22301139       -13    -4.5    🚩
Malik Beasley           0.0          12.0  MIL  2023-11-03  NYK  22300002         5    -5.5    🚩
Malik Beasley           0.0          11.9  MIL  2023-12-25  NYK  22300401        -7    -3.0    🚩

In [363]:
team = 'MIN'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                       
Anthony Edwards      9.0          25.9  MIN  2024-01-22  CHA  22300610        -3   -14.0    🚩
Anthony Edwards     11.0          26.6  MIN  2024-03-01  SAC  22300862        -4    -8.5    🚩
Anthony Edwards     13.0          26.3  MIN  2024-03-04  POR  22300881         5   -15.0    🚩
Anthony Edwards      9.0          26.4  MIN  2024-03-27  DET  22301056        15   -16.5    🚩
Anthony Edwards     14.0          26.3  MIN  2024-04-12  ATL  22301178         3   -12.5    🚩
Anthony Edwards     13.0          26.1  MIN  2024-04-14  PHX  22301194       -19    -2.0    🚩
Jaden McDaniels      0.0          10.9  MIN  2023-11-14  GSW  22300025         3    -3.5    🚩
Karl-Anthony Towns  10.0          22.0  MIN  2023-12-28  DAL  22300423         8   -12.0    🚩
Karl-Anthony Towns   9.0          21.6  MIN  2023-12-30  LAL  22300443         2    -4.5    🚩
Karl-Anthony Towns  11.0          22.1  MIN  2024-04-12  ATL  22301178         3   -12.5    🚩
Karl-Anthony Towns  10.0          22.0  MIN  2024-04-14  PHX  22301194       -19    -2.0    🚩
Mike Conley          0.0          10.7  MIN  2024-03-03  LAC  22300873        -1    -2.5    🚩
Naz Reid             3.0          13.6  MIN  2024-04-09  WAS  22301152         9   -18.0    🚩

In [364]:
team = 'NOP'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                      
Brandon Ingram      8.0          23.6  NOP  2023-12-15  CHA  22300326         5    -9.5    🚩
CJ McCollum        13.0          23.4  NOP  2023-11-04  ATL  22300135       -18    -2.0    🚩
CJ McCollum         2.0          19.0  NOP  2024-02-23  MIA  22300810       -11    -2.0    🚩
CJ McCollum         8.0          18.3  NOP  2024-03-13  CLE  22300951       -21    -6.0    🚩
Jonas Valanciunas   2.0          12.3  NOP  2024-04-14  LAL  22301195       -16    -2.0    🚩
Jordan Hawkins      0.0          11.5  NOP  2023-12-15  CHA  22300326         5    -9.5    🚩
Zion Williamson    12.0          23.0  NOP  2024-04-14  LAL  22301195       -16    -2.0    🚩

In [365]:
team = 'NYK'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                     
Immanuel Quickley  5.0          16.3  NYK  2023-11-30  DET  22300268         6   -14.5    🚩
RJ Barrett         9.0          20.5  NYK  2023-11-26  PHX  22300247        -3    -6.5    🚩
RJ Barrett         9.0          19.6  NYK  2023-12-13  UTA  22300318        -4    -6.0    🚩

In [366]:
team = 'OKC'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                            
Chet Holmgren             4.0          17.6  OKC  2023-12-06  HOU  22301212        -9    -1.5    🚩
Chet Holmgren             4.0          17.0  OKC  2024-01-29  MIN  22300664        -6    -2.5    🚩
Chet Holmgren             7.0          17.2  OKC  2024-03-08  MIA  22300914         7    -8.5    🚩
Chet Holmgren             2.0          16.9  OKC  2024-03-27  HOU  22301057        -6    -5.0    🚩
Chet Holmgren             5.0          16.8  OKC  2024-03-31  NYK  22301082         1    -2.0    🚩
Jalen Williams            7.0          19.3  OKC  2024-03-04  LAL  22300884       -12    -1.0    🚩
Shai Gilgeous-Alexander  20.0          31.2  OKC  2024-03-04  LAL  22300884       -12    -1.0    🚩
Shai Gilgeous-Alexander  20.0          31.1  OKC  2024-03-16  MEM  22300972         6   -10.5    🚩
Shai Gilgeous-Alexander  19.0          30.4  OKC  2024-03-31  NYK  22301082         1    -2.0    🚩

In [367]:
team = 'ORL'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                   
Cole Anthony     4.0          15.9  ORL  2023-12-01  WAS  22300274         5   -10.5    🚩
Jalen Suggs      0.0          12.9  ORL  2024-01-26  MEM  22300638        -1    -6.0    🚩
Paolo Banchero  10.0          21.1  ORL  2023-12-20  MIA  22300366        -9    -5.5    🚩

In [368]:
team = 'PHI'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                  
Cameron Payne   2.0          13.7  PHI  2024-02-14  MIA  22300779        -5    -2.5    🚩
Tobias Harris   6.0          18.0  PHI  2023-12-06  WAS  22301208         5   -10.5    🚩
Tobias Harris   3.0          16.8  PHI  2023-12-18  CHI  22300351        -4   -10.5    🚩
Tobias Harris   5.0          17.3  PHI  2024-01-05  NYK  22300483       -36    -6.0    🚩
Tobias Harris   7.0          17.7  PHI  2024-02-22  NYK  22300794       -14    -1.5    🚩
Tyrese Maxey   16.0          26.2  PHI  2024-01-20  CHA  22300593         8   -12.0    🚩

In [369]:
team = 'PHX'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                  
Bradley Beal    6.0          16.4  PHX  2023-12-15  NYK  22300333       -17    -5.0    🚩
Bradley Beal    7.0          18.2  PHX  2024-03-02  HOU  22300870        -9    -9.0    🚩
Devin Booker    8.0          29.4  PHX  2023-11-29  TOR  22300260        -7    -3.5    🚩
Devin Booker   16.0          26.6  PHX  2024-01-16  SAC  22300567         2    -4.5    🚩
Devin Booker   16.0          27.0  PHX  2024-01-22  CHI  22300612         2    -5.0    🚩
Devin Booker   14.0          27.2  PHX  2024-03-29  OKC  22301069       -25    -2.5    🚩
Devin Booker   12.0          27.3  PHX  2024-04-09  LAC  22301156       -13    -9.5    🚩
Eric Gordon     0.0          14.0  PHX  2023-12-31  ORL  22300450         5    -5.5    🚩
Eric Gordon     3.0          13.2  PHX  2024-01-14  POR  22300554        11   -14.5    🚩
Grayson Allen   2.0          12.9  PHX  2024-03-02  HOU  22300870        -9    -9.0    🚩
Josh Okogie     0.0          11.2  PHX  2023-11-02  SAS  22300131       -11   -10.5    🚩
Kevin Durant   16.0          30.9  PHX  2023-12-25  DAL  22300405       -14    -4.0    🚩
Kevin Durant   15.0          28.8  PHX  2024-01-28  ORL  22300655       -15    -2.0    🚩
Kevin Durant   11.0          28.1  PHX  2024-03-17  MIL  22300976       -11    -2.5    🚩

In [370]:
team = 'POR'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                    
Anfernee Simons   9.0          28.5  POR  2023-12-14  UTA  22300323        -8    -5.0    🚩
Anfernee Simons  10.0          23.3  POR  2024-02-25  CHA  22300826       -13    -3.5    🚩
Shaedon Sharpe    4.0          18.8  POR  2023-12-14  UTA  22300323        -8    -5.0    🚩

In [371]:
team = 'SAC'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                     
De'Aaron Fox      14.0          31.9  SAC  2023-11-20  NOP  22300222       -36    -1.5    🚩
De'Aaron Fox      15.0          30.0  SAC  2024-01-03  ORL  22300476         3    -5.5    🚩
De'Aaron Fox      12.0          27.8  SAC  2024-02-07  DET  22300732       -13   -13.5    🚩
Domantas Sabonis  10.0          20.8  SAC  2023-11-20  NOP  22300222       -36    -1.5    🚩
Domantas Sabonis   9.0          19.9  SAC  2023-11-28  GSW  22300060         1    -2.0    🚩
Harrison Barnes   10.0          33.0  SAC  2023-10-27  GSW  22300087        -8    -3.0    🚩
Harrison Barnes    3.0          15.6  SAC  2023-11-06  HOU  22300153       -25    -2.0    🚩
Keegan Murray      5.0          16.2  SAC  2023-12-26  POR  22300413       -17    -9.0    🚩
Keegan Murray      5.0          16.2  SAC  2024-01-29  MEM  22300663         9   -11.0    🚩
Keegan Murray      0.0          15.7  SAC  2024-02-07  DET  22300732       -13   -13.5    🚩
Keegan Murray      3.0          15.1  SAC  2024-03-07  SAS  22300908         2   -12.0    🚩
Kevin Huerter      0.0          10.7  SAC  2024-03-07  SAS  22300908         2   -12.0    🚩
Kevin Huerter      0.0          10.5  SAC  2024-03-16  NYK  22300975        -7    -3.0    🚩
Kevin Huerter      0.0          10.3  SAC  2024-03-18  MEM  22300989        10   -11.5    🚩
Malik Monk         3.0          14.9  SAC  2024-01-29  MEM  22300663         9   -11.0    🚩

In [372]:
team = 'TOR'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                   
Dennis Schroder  4.0          16.7  TOR  2023-11-13  WAS  22300189         4    -8.0    🚩
Gary Trent Jr.   0.0          11.2  TOR  2023-12-08  CHA  22301216        -3    -5.5    🚩
Scottie Barnes   7.0          20.1  TOR  2024-02-12  SAS  22300764       -23    -6.0    🚩

In [373]:
team = 'UTA'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                                    
Collin Sexton     1.0          12.5  UTA  2023-11-22  POR  22300237       -16    -3.5    🚩
Collin Sexton     6.0          17.5  UTA  2024-01-29  BKN  22300660       -33    -1.0    🚩
Lauri Markkanen  13.0          23.8  UTA  2024-01-29  BKN  22300660       -33    -1.0    🚩

In [374]:
team = 'WAS'
FLAG = []
resultsDF = pd.DataFrame()
for i in range (len(resultsDict[team])):
    resultsDF = pd.concat([resultsDF,pd.DataFrame(resultsDict[team][i])],axis=0)
for i in range(len(resultsDF)):
    if 10+resultsDF.iloc[i]['PTS'] < resultsDF.iloc[i]['PREV AVG PTS']:
        FLAG.append('🚩')
    else: FLAG.append(' ')
resultsDF['FLAG'] = FLAG
allDF = allDF.append(resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER'))
resultsDF[resultsDF['FLAG'] == '🚩'].sort_values(by='PLAYER')

PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
PLAYER                                                                               
Kyle Kuzma  11.0          22.2  WAS  2024-01-20  SAS  22300594        -4    -2.0    🚩
Kyle Kuzma  12.0          22.4  WAS  2024-03-29  DET  22301065        -9    -3.5    🚩

In [384]:
allDF.reset_index()

PLAYER   PTS  PREV AVG PTS TEAM        DATE OPPT    GAMEID  PTSDELTA  SPREAD FLAG
0               Jalen Johnson   5.0          15.4  ATL  2024-01-13  WAS  22300543       -28    -8.0    🚩
1                  Saddiq Bey   2.0          12.1  ATL  2023-11-09  ORL  22300172         1    -3.5    🚩
2                  Trae Young  13.0          27.8  ATL  2024-01-12  IND  22300533       -18    -6.0    🚩
3                  Trae Young  12.0          27.0  ATL  2024-02-14  CHA  22300777       -23    -7.0    🚩
4                  Trae Young  11.0          26.7  ATL  2024-02-23  TOR  22300804        -2    -7.5    🚩
5                  Trae Young  14.0          26.4  ATL  2024-04-10  CHA  22301159        -1    -8.5    🚩
6                  Cam Thomas   9.0          20.7  BKN  2024-01-07  POR  22300498        -7    -9.0    🚩
7                  Cam Thomas   8.0          20.6  BKN  2024-01-17  POR  22300578        -2    -5.0    🚩
8            Lonnie Walker IV   0.0          14.0  BKN  2024-01-07  POR  22300498        -7    -9.0    🚩
9            Lonnie Walker IV   0.0          12.0  BKN  2024-01-27  HOU  22300645         2    -4.0    🚩
10              Derrick White   2.0          16.0  BOS  2024-01-27  LAC  22300646       -19    -7.0    🚩
11              Derrick White   3.0          15.5  BOS  2024-03-05  CLE  22300886        -1    -8.5    🚩
12              Derrick White   4.0          15.8  BOS  2024-02-09  WAS  22300743         4   -18.0    🚩
13              Derrick White   2.0          15.4  BOS  2024-04-11  NYK  22301167        -9    -3.5    🚩
14               Jaylen Brown  12.0          22.9  BOS  2023-11-19  MEM  22300213         2   -12.0    🚩
15               Jaylen Brown   8.0          22.5  BOS  2024-01-27  LAC  22300646       -19    -7.0    🚩
16               Jaylen Brown   8.0          22.2  BOS  2024-02-01  LAL  22300684        -9   -15.5    🚩
17               Jaylen Brown  11.0          23.2  BOS  2023-11-08  PHI  22300159        -3    -2.5    🚩
18               Jayson Tatum  17.0          28.5  BOS  2023-11-17  TOR  22300031         3    -9.0    🚩
19               Jayson Tatum  15.0          27.3  BOS  2023-12-19  GSW  22300362        -6    -5.0    🚩
20               Jayson Tatum  17.0          27.2  BOS  2024-04-05  SAC  22301118         1    -9.5    🚩
21               Jayson Tatum  15.0          27.1  BOS  2024-03-07  DEN  22300906        -6    -2.0    🚩
22               Jayson Tatum  16.0          30.5  BOS  2023-11-08  PHI  22300159        -3    -2.5    🚩
23               Jayson Tatum  22.0          34.0  BOS  2023-10-27  MIA  22300080         8    -8.5    🚩
24               Jrue Holiday   2.0          12.6  BOS  2024-04-01  CHA  22301087        14   -18.5    🚩
25         Kristaps Porzingis   9.0          19.6  BOS  2023-11-24  ORL  22300043       -17    -5.0    🚩
26         Kristaps Porzingis  17.0          30.0  BOS  2023-10-27  MIA  22300080         8    -8.5    🚩
27             Gordon Hayward   4.0          15.1  CHA  2023-11-22  WAS  22300225         3    -3.5    🚩
28              Mark Williams   2.0          13.0  CHA  2023-10-27  DET  22300077       -12    -4.5    🚩
29            P.J. Washington  13.0          25.0  CHA  2023-10-27  DET  22300077       -12    -4.5    🚩
30                 Coby White   0.0          16.0  CHI  2023-10-28  DET  22300088       -16    -2.5    🚩
31             Nikola Vucevic   5.0          18.0  CHI  2024-04-01  ATL  22301091       -12    -2.0    🚩
32                Zach LaVine  10.0          20.5  CHI  2024-01-13  SAS  22300548         6    -7.0    🚩
33               Caris LeVert   6.0          17.5  CLE  2023-11-25  LAL  22300242        -6    -4.0    🚩
34               Caris LeVert   5.0          15.5  CLE  2023-11-30  POR  22300265        -8   -12.5    🚩
35               Caris LeVert   4.0          15.3  CLE  2024-02-07  WAS  22300728         8   -11.5    🚩
36             Darius Garland   6.0          20.3  CLE  2023-11-25  LAL  22300242        -6    -4.0    🚩
37             Darius Garland   9

In [391]:
np.unique(allDF.reset_index()['TEAM'],return_counts=True)

(array(['ATL', 'BKN', 'BOS', 'CHA', 'CHI', 'CLE', 'DAL', 'DEN', 'DET',
        'GSW', 'HOU', 'IND', 'LAC', 'LAL', 'MEM', 'MIA', 'MIL', 'MIN',
        'NOP', 'NYK', 'OKC', 'ORL', 'PHI', 'PHX', 'POR', 'SAC', 'TOR',
        'UTA', 'WAS'], dtype=object),
 array([ 6,  4, 17,  3,  3, 15, 12, 13,  2,  7,  6, 10, 10, 11,  1,  7, 11,
        13,  7,  3,  9,  3,  6, 14,  3, 15,  3,  3,  2]))

In [383]:
pd.DataFrame(np.unique(allDF.reset_index()['PLAYER'],return_counts=True)).T.rename(columns={0:'PLAYER',1:'COUNT'}).sort_values(by='COUNT',ascending=False).reset_index(drop=True)

PLAYER COUNT
0                Jayson Tatum     6
1             Anthony Edwards     6
2            Donovan Mitchell     6
3                Devin Booker     5
4            Tim Hardaway Jr.     5
5               Stephen Curry     5
6               Chet Holmgren     5
7                 Paul George     4
8                Jaylen Brown     4
9          Karl-Anthony Towns     4
10              Keegan Murray     4
11              Derrick White     4
12                Luka Doncic     4
13             Damian Lillard     4
14                Jalen Green     4
15           D'Angelo Russell     4
16              Tobias Harris     4
17                 Trae Young     4
18               Caris LeVert     3
19          Tyrese Haliburton     3
20               Kevin Durant     3
21              Kevin Huerter     3
22              Anthony Davis     3
23         Bennedict Mathurin     3
24    Shai Gilgeous-Alexander     3
25               De'Aaron Fox     3
26             Darius Garland     3
27                CJ McCollum     3
28             Reggie Jackson     3
29               James Harden     3
30                  Max Strus     3
31               Nikola Jokic     3
32      Giannis Antetokounmpo     3
33   Kentavious Caldwell-Pope     2
34              Aaron Nesmith     2
35                 Kyle Kuzma     2
36         Kristaps Porzingis     2
37                 RJ Barrett     2
38             Taurean Prince     2
39           Lonnie Walker IV     2
40              Malik Beasley     2
41               Jamal Murray     2
42               Aaron Gordon     2
43                 Cam Thomas     2
44               Bradley Beal     2
45           Domantas Sabonis     2
46            Duncan Robinson     2
47                Eric Gordon     2
48            Harrison Barnes     2
49              Collin Sexton     2
50            Anfernee Simons     2
51               Bobby Portis     1
52                 Obi Toppin     1
53               Cole Anthony     1
54         Michael Porter Jr.     1
55                Mike Conley     1
56               Myles Turner     1
57                   Naz Reid     1
58                Zach LaVine     1
59               Tyrese Maxey     1
60                 Coby White     1
61             Nikola Vucevic     1
62              Norman Powell     1
63             Alperen Sengun     1
64            P.J. Washington     1
65           Bojan Bogdanovic     1
66             Paolo Banchero     1
67              Cameron Payne     1
68              Mark Williams     1
69               Caleb Martin     1
70              Rui Hachimura     1
71                 Saddiq Bey     1
72             Scottie Barnes     1
73             Shaedon Sharpe     1
74             Brandon Ingram     1
75                Bam Adebayo     1
76           Jaime Jaquez Jr.     1
77            Dennis Schroder     1
78                 Malik Monk     1
79                Josh Okogie     1
80            Jaden McDaniels     1
81              Jalen Johnson     1
82                Jalen Suggs     1
83             Jalen Williams     1
84           Jabari Smith Jr.     1
85                Ivica Zubac     1
86          Jaren Jackson Jr.     1
87          Immanuel Quickley     1
88               Jimmy Butler     1
89          Jonas Valanciunas     1
90           Jonathan Kuminga     1
91             Jordan Hawkins     1
92               Jrue Holiday     1
93                Jalen Duren     1
94              Grayson Allen     1
95              Kawhi Leonard     1
96             Grant Williams     1
97             Gordon Hayward     1
98             Gary Trent Jr.     1
99                 Kevin Love     1
100           Khris Middleton     1
101             Klay Thompson     1
102              Kyrie Irving     1
103           Lauri Markkanen     1
104              LeBron James     1
105         Derrick Jones Jr.     1
106           Zion Williamson     1

In [237]:
################################################
################################################
################################################
################################################
################################################
STOP

NameError: name 'STOP' is not defined

In [ ]:
GAMEID = str(22300104)
boxScoreDF = pd.read_csv('/Users/olutosinfashusi/jupyter/csv/boxScoreCSV/boxScoreCSVs/'+ GAMEID +'.csv')#.fillna(' ')
boxScoreDF = boxScoreDF[boxScoreDF['TEAM'] == team]
boxScoreDF.insert(1,'OPPT',teamDF.iloc[i]['OPPT'])
boxScoreDF = boxScoreDF.reset_index(drop=True).dropna()
boxScoreDF = cleanBoxScore(boxScoreDF);
boxScoreDF

In [ ]:
results = []

In [ ]:
for i in range (len(teamDF)):
    GAMEID = teamDF.iloc[i]['GAMEID']
    GAMEID = str(GAMEID)
    print(GAMEID)
    boxScoreDF = pd.read_csv('/Users/olutosinfashusi/jupyter/csv/boxScoreCSV/boxScoreCSVs/'+ GAMEID +'.csv')#.fillna(' ')
    boxScoreDF = boxScoreDF[boxScoreDF['TEAM'] == 'ATL']
    boxScoreDF.insert(1,'OPPT',teamDF.iloc[i]['OPPT'])
    boxScoreDF = boxScoreDF.reset_index(drop=True).dropna()
    boxScoreDF = cleanBoxScore(boxScoreDF);
    
    prevGamesDF = NBAdf[NBAdf['TEAM'] == 'ATL']
    prevGamesDF  = prevGamesDF[prevGamesDF['GAME DATE'] < teamDF.iloc[i]['GAME DATE']]
    prevGamesDF.reset_index(drop=True);

    prevGameIDs = prevGamesDF['GAMEID'].values
    prevOppts = prevGamesDF['OPPT'].values

    prevBoxScoresDF = pd.DataFrame()
    for prevIter in range (len(prevGameIDs)):
        GAMEID = str(prevGameIDs[prevIter])
        prevBoxScoreDF = pd.read_csv('/Users/olutosinfashusi/jupyter/csv/boxScoreCSV/boxScoreCSVs/'+ GAMEID +'.csv')#.fillna(' ')
        prevBoxScoreDF = prevBoxScoreDF[prevBoxScoreDF['TEAM'] == 'ATL']
        prevBoxScoreDF.insert(1,'OPPT',prevOppts[prevIter])
        prevBoxScoreDF = cleanBoxScore(prevBoxScoreDF)
        prevBoxScoresDF = pd.concat([prevBoxScoresDF,prevBoxScoreDF],axis=0)

    prevBoxScoresDF.groupby("PLAYER")['PTS'].mean()
    boxScoreDF.groupby("PLAYER")['PTS'].mean()
    prevAVGPTS = pd.DataFrame(prevBoxScoresDF.groupby("PLAYER")['PTS'].mean())

    prevAVGPTS = prevAVGPTS.rename(columns={'PTS':'PREV AVG PTS'})
    df = pd.concat([boxScoreDF.groupby("PLAYER")['PTS'].mean(),
           prevAVGPTS.groupby("PLAYER")['PREV AVG PTS'].mean()],axis=1).dropna()
    df['DATE'] = teamDF.iloc[i]['GAME DATE']
    df['TEAM'] = teamDF.iloc[i]['TEAM']
    df['OPPT'] = teamDF.iloc[i]['OPPT']
    results.append(df)
    pd.concat(results)

In [ ]:
pd.concat(results)

In [ ]:
#boxScoreDF

In [ ]:
prevBoxScoreDF.groupby('PLAYER')['PTS'].mean()

In [ ]:
type(prevBoxScoreDF.iloc[0]['PTS'])

In [ ]:
#pd.concat(results)

In [ ]:
prevBoxScoresDF.groupby("PLAYER")['PTS'].mean()

In [ ]:
ATLF.iloc[0].to_frame().T['GAMEID'].values[0]

In [ ]:
GAMEID = str(ATLF.iloc[0].to_frame().T['GAMEID'].values[0])


In [ ]:
pd.read_csv('/Users/olutosinfashusi/jupyter/csv/boxScoreCSV/boxScoreCSVs/'+ GAMEID +'.csv').fillna(' ')

In [ ]:
NBAdf.head(1)['GAME DATE'].values

In [ ]:
NBAdf[(NBAdf['TEAM'] == 'TOR') 
               & (NBAdf['OPPT'] == 'SAC') 
               & (NBAdf['GAME DATE'] == datetime.date(2024,3,20))]

In [ ]:
NBAdf[(NBAdf['TEAM'] == 'TOR') 
               & (NBAdf['OPPT'] == 'LAC') 
               & (NBAdf['GAME DATE'] == datetime.date(2024,1,26))]

In [ ]:
GAMEID = NBAdf[(NBAdf['TEAM'] == 'TOR') 
               & (NBAdf['OPPT'] == 'LAC') 
               & (NBAdf['GAME DATE'] == datetime.date(2024,1,26))]['GAMEID'].values[0]
GAMEID = str(GAMEID)
pd.read_csv('/Users/olutosinfashusi/jupyter/csv/boxScoreCSV/boxScoreCSVs/'+GAMEID +'.csv').fillna(' ')

In [ ]:
#irisDF[~(irisDF['petal_width'] <= 1.75) & (irisDF['petal_length'] <= 4.85)]
GAMEID = NBAdf[(NBAdf['TEAM'] == 'TOR') 
               & (NBAdf['OPPT'] == 'SAC') 
               & (NBAdf['GAME DATE'] == datetime.date(2024,3,20))]['GAMEID'].values[0]
GAMEID = str(GAMEID)
print(GAMEID)

In [ ]:
pd.read_csv('/Users/olutosinfashusi/jupyter/csv/boxScoreCSV/boxScoreCSVs/'+GAMEID +'.csv').fillna(' ')